In [543]:
import pandas as pd
import statsmodels.api as sm

In [544]:
df = pd.read_csv(r'./owid-2022-clean.csv')

In [545]:
# Drop irrelevant fields
print(df.columns.shape)
df.drop(["location", "date", "total_deaths_per_million", "total_cases_per_million", "population", "tests_units"], axis=1, inplace=True)

print(df.columns.shape)

(31,)
(25,)


In [546]:
# applied_cols = list(df.columns)
# df_group_iso = df.groupby(["iso_code"])
# for col_name, col_data in df.iteritems():
#     if col_name == "iso_code" or col_name=="continent":
#         continue
#     df[col_name] = df_group_iso[col_name].apply(lambda x: x.fillna(x.mean()))


# df_group_cont = df.groupby(["continent"])
# for col_name, col_data in df.iteritems():
#     if col_name == "iso_code" or col_name=="continent":
#         continue
#     df[col_name] = df_group_cont[col_name].apply(lambda x: x.fillna(x.mean()))
#     print(col_data, (col_data == 0).all())

In [547]:
applied_cols = list(df.columns)
df_group_iso = df.groupby(["iso_code"])
df_group_cont = df.groupby(["continent"])




for col_name, col_data in df.iteritems():
    if col_name == "iso_code" or col_name=="continent":
        continue
    # replace nan with country median
    df[col_name] = df_group_iso[col_name].apply(lambda x: x.fillna(x.median()))
    # replace nan with continent median
    df[col_name] = df_group_cont[col_name].apply(lambda x: x.fillna(x.median()))

# Only replace zero values when the entire column of the country is 0. This is because countries like Vietnam have days where no deaths are recorded, but other days still record a positive number. This is different to countries where no death numbers are recorded.
df_group_cont_med = df_group_cont.median()
for col_name, col_data in df_group_iso:    
    for col in col_data:
        if (col_data[col] == 0).all():
            target = df.loc[df["iso_code"] == col_name]
            df.loc[df["iso_code"] == col_name, col] = target[col].replace(0, df_group_cont_med.at[target["continent"].iloc[0], col])



In [548]:
indicator_cols = pd.get_dummies(df[ "continent"])
df = pd.concat([df, indicator_cols], axis=1)
df.drop(["iso_code", "continent"], axis=1, inplace=True)

In [549]:
df.to_csv("./data.csv")

In [550]:
def linear_regression(X: pd.DataFrame, y: pd.DataFrame, ft_in_use):
    X = X[ft_in_use]
   

    model = sm.OLS(y, sm.add_constant(X))
    results = model.fit()
    print(results.summary())

    y_pred = results.predict(sm.add_constant(X))
    print(f'MSE: {sum((y - y_pred) ** 2) / len(y)}')
    return results

In [551]:
# process data here
df = pd.read_csv('data.csv')

ft_predict = ['new_deaths_per_million', 'new_cases_per_million']
ft_ignore = ['iso_code', 'location', 'date', 'total_deaths', 'total_cases_per_million', 'total_deaths_per_million', 'population', 'tests_units'] # add ignore column names here

features = list(set(df.columns).difference(ft_predict + ft_ignore))

y = df[ft_predict]
X = df[features]

In [552]:
def new_deaths_per_million(X: pd.DataFrame, y: pd.DataFrame, ft_in_use):
    return linear_regression(X, y['new_deaths_per_million'], ft_in_use)

In [553]:
def new_cases_per_million(X: pd.DataFrame, y: pd.DataFrame, ft_in_use):
    return linear_regression(X, y['new_cases_per_million'], ft_in_use)

In [554]:
# ordinary linear regression

dth = new_deaths_per_million(X, y, features)
cas = new_cases_per_million(X, y, features)

c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)


                              OLS Regression Results                              
Dep. Variable:     new_deaths_per_million   R-squared:                       0.443
Model:                                OLS   Adj. R-squared:                  0.346
Method:                     Least Squares   F-statistic:                     4.569
Date:                    Sat, 04 Jun 2022   Prob (F-statistic):           1.05e-59
Time:                            20:02:46   Log-Likelihood:                -3517.9
No. Observations:                    1323   AIC:                             7430.
Df Residuals:                        1126   BIC:                             8452.
Df Model:                             196                                         
Covariance Type:                nonrobust                                         
                                          coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------

c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)


In [555]:
# reorder columns according to p-values
# save to `features` variable

deaths_ft = sorted(features, key=lambda col: dth.pvalues[col])
cases_ft = sorted(features, key=lambda col: cas.pvalues[col])

alpha = 0.05

In [556]:
# stepwise forward regression

def forward_reg(title, features, func):
    if (title is not None):
        print(title)
    
    ft_in_use = []
    for col in features:
        ft_in_use.append(col)

        res = func(X, y, ft_in_use)

        print(f'Added ft:  {col}')
        print(f'Ft in use: {ft_in_use}')

        if (max(res.pvalues) > alpha):
            print(f'Break due to stopping rule: max pvalue = {max(res.pvalues)} > {alpha}')
            break

        print('*' * 20)

In [557]:
# stepwise forward regression
forward_reg('New deaths per million model:', deaths_ft, new_deaths_per_million)
forward_reg('New cases per million model:', cases_ft, new_cases_per_million)

New deaths per million model:
                              OLS Regression Results                              
Dep. Variable:     new_deaths_per_million   R-squared:                       0.073
Model:                                OLS   Adj. R-squared:                  0.073
Method:                     Least Squares   F-statistic:                     104.6
Date:                    Sat, 04 Jun 2022   Prob (F-statistic):           1.10e-23
Time:                            20:02:47   Log-Likelihood:                -3854.5
No. Observations:                    1323   AIC:                             7713.
Df Residuals:                        1321   BIC:                             7723.
Df Model:                               1                                         
Covariance Type:                nonrobust                                         
                    coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------

c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.p

In [558]:
# stepwise backward regression

def backward_reg(title, features, func):
    if (title is not None):
        print(title)
    
    ft_in_use = features
    for col in features:
        ft_in_use.remove(col)

        res = func(X, y, ft_in_use)

        print(f'Removed ft:  {col}')
        print(f'Ft in use: {ft_in_use}')

        if (max(res.pvalues) < alpha):
            print(f'Break due to stopping rule: max pvalue = {max(res.pvalues)} < {alpha}')
            break

        print('*' * 20)


In [559]:
# stepwise backward regression
backward_reg('New deaths per million model:', deaths_ft, new_deaths_per_million)
backward_reg('New cases per million model:', cases_ft, new_cases_per_million)

New deaths per million model:
                              OLS Regression Results                              
Dep. Variable:     new_deaths_per_million   R-squared:                       0.439
Model:                                OLS   Adj. R-squared:                  0.341
Method:                     Least Squares   F-statistic:                     4.514
Date:                    Sat, 04 Jun 2022   Prob (F-statistic):           1.63e-58
Time:                            20:02:47   Log-Likelihood:                -3523.1
No. Observations:                    1323   AIC:                             7438.
Df Residuals:                        1127   BIC:                             8455.
Df Model:                             195                                         
Covariance Type:                nonrobust                                         
                                          coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------

c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)


MSE: 12.038375822559628
Removed ft:  positive_rate
Ft in use: ['new_tests_smoothed_per_thousand', 'iso_code_CYP', 'iso_code_HKG', 'iso_code_MLT', 'iso_code_GTM', 'iso_code_PRT', 'iso_code_ALB', 'iso_code_PAN', 'iso_code_ARM', 'iso_code_ROU', 'iso_code_GRD', 'iso_code_STP', 'iso_code_PSE', 'iso_code_CZE', 'iso_code_BHS', 'iso_code_UZB', 'iso_code_MUS', 'iso_code_DZA', 'iso_code_EST', 'iso_code_DJI', 'iso_code_GNQ', 'iso_code_CMR', 'iso_code_SYC', 'iso_code_ETH', 'iso_code_BOL', 'iso_code_URY', 'iso_code_MDA', 'iso_code_SAU', 'continent_Oceania', 'continent_North America', 'population_density', 'iso_code_WSM', 'iso_code_AUT', 'iso_code_LKA', 'iso_code_TON', 'iso_code_ESP', 'iso_code_RWA', 'iso_code_BIH', 'iso_code_NIC', 'iso_code_BRB', 'iso_code_TJK', 'iso_code_TUN', 'iso_code_KWT', 'iso_code_TCD', 'iso_code_NPL', 'iso_code_BFA', 'iso_code_PER', 'iso_code_VNM', 'iso_code_TLS', 'iso_code_MAR', 'iso_code_USA', 'iso_code_IRQ', 'continent_Europe', 'iso_code_LSO', 'iso_code_AUS', 'iso_code_AF

c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)


                              OLS Regression Results                              
Dep. Variable:     new_deaths_per_million   R-squared:                       0.439
Model:                                OLS   Adj. R-squared:                  0.341
Method:                     Least Squares   F-statistic:                     4.514
Date:                    Sat, 04 Jun 2022   Prob (F-statistic):           1.63e-58
Time:                            20:02:47   Log-Likelihood:                -3523.1
No. Observations:                    1323   AIC:                             7438.
Df Residuals:                        1127   BIC:                             8455.
Df Model:                             195                                         
Covariance Type:                nonrobust                                         
                                          coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------

...

c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)


MSE: 1918333.345331143
Removed ft:  people_vaccinated_per_hundred
Ft in use: ['iso_code_HKG', 'iso_code_SGP', 'hospital_beds_per_thousand', 'iso_code_COL', 'iso_code_VUT', 'iso_code_AND', 'continent_North America', 'iso_code_FIN', 'continent_Asia', 'iso_code_SLE', 'iso_code_TUR', 'iso_code_COG', 'iso_code_PER', 'iso_code_GBR', 'iso_code_TUN', 'iso_code_ATG', 'iso_code_LKA', 'iso_code_ERI', 'iso_code_ARE', 'iso_code_ZMB', 'iso_code_COD', 'iso_code_BRN', 'iso_code_SSD', 'iso_code_AGO', 'iso_code_PAN', 'iso_code_GHA', 'iso_code_BEL', 'iso_code_VNM', 'iso_code_MDG', 'iso_code_SVK', 'iso_code_UGA', 'iso_code_BHS', 'aged_65_older', 'iso_code_KWT', 'iso_code_SRB', 'iso_code_HRV', 'iso_code_IRN', 'iso_code_ECU', 'iso_code_MRT', 'iso_code_AFG', 'iso_code_DZA', 'iso_code_ESP', 'iso_code_GNQ', 'iso_code_NGA', 'iso_code_TCD', 'iso_code_CHE', 'iso_code_SMR', 'iso_code_EST', 'iso_code_KNA', 'iso_code_YEM', 'iso_code_PRT', 'iso_code_CPV', 'iso_code_UKR', 'iso_code_BGR', 'iso_code_EGY', 'iso_code_CAF'

c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)


                              OLS Regression Results                             
Dep. Variable:     new_cases_per_million   R-squared:                       0.443
Model:                               OLS   Adj. R-squared:                  0.393
Method:                    Least Squares   F-statistic:                     8.863
Date:                   Sat, 04 Jun 2022   Prob (F-statistic):           1.79e-94
Time:                           20:03:36   Log-Likelihood:                -11454.
No. Observations:                   1323   AIC:                         2.313e+04
Df Residuals:                       1213   BIC:                         2.370e+04
Df Model:                            109                                         
Covariance Type:               nonrobust                                         
                                          coef    std err          t      P>|t|      [0.025      0.975]
----------------------------------------------------------------------------

c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
c:\Users\Ashimory\anaconda3\lib\site-packages\statsmodels\tsa\tsatools.py:142: FutureWarning: In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.
  x = pd.concat(x[::order], 1)
